this notebook is for trying out small BERTopic models (2000 messages each) per different word_counts and then comparing them. If it works, this will be the procedure. 

1. cut df into word count ranges

In [1]:
import pandas as pd
df = pd.read_csv('path/to/textanal_short.csv')


### step 1: cut df into word count ranges

In [9]:
contains_floats_df = df['text_clean'].apply(lambda x: isinstance(x, float)).any()

if contains_floats_df:
    print("The column contains float values.")
    df = df[~df['text_clean'].apply(lambda x: isinstance(x, float))]
else:
    print("No float values in 'text_clean'.")

No float values in 'text_clean'.


In [5]:
import pandas as pd
import numpy as np

# Assuming df is your DataFrame and it already includes a 'word_count' column

# Corrected Define the word count bins and their labels
bins = [5, 10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, 130, 150, 170, 200, 250, np.inf]
labels = ['5-10', '11-20', '21-30', '31-40', '41-50', '51-60', '61-70', '71-80', '81-90', '91-100', '101-110', '111-130', '131-150', '151-170', '171-200', '201-250', '251+']

# Categorize each message into word count ranges
df['word_count_range'] = pd.cut(df['word_count'], bins=bins, labels=labels, right=False)


In [2]:
!pip freeze > requirements.txt

subsamples holds df with the ranges

In [8]:
# Function to sample messages from each range
def sample_messages(df, word_count_range):
    return df[df['word_count_range'] == word_count_range].sample(n=2000, random_state=1)

# Dictionary to hold the subsamples for each word count range
subsamples = {}

for label in labels:
    # Attempt to sample 5,000 messages from each range
    try:
        subsamples[label] = sample_messages(df, label)
    except ValueError:
        # If the range has fewer than 5,000 messages, take all messages from that range
        subsamples[label] = df[df['word_count_range'] == label]
        print(f"Not enough messages in range {label}. Took all available messages.")

# At this point, `subsamples` is a dictionary where each key is a word count range (label)
# and each value is a DataFrame containing the subsample of 2,000 messages for that range.


### step 2 prepare text for BERT and run for each subsample

### step 3 now run BERTopic for each subsample


In [16]:
import nltk
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import CountVectorizer
from sentence_transformers import SentenceTransformer
from umap import UMAP
from hdbscan import HDBSCAN
from bertopic import BERTopic

# Download stopwords and combine them
nltk.download('stopwords')
stopwords_combined = stopwords.words('german') + stopwords.words('french') + \
                      stopwords.words('spanish') + stopwords.words('english')

# Initialize Sentence Transformer Model
model = SentenceTransformer("all-MiniLM-L6-v2")

# Prepare UMAP and HDBSCAN models
umap_model = UMAP(n_neighbors=10, n_components=5, min_dist=0.0, metric='cosine', random_state=42)
hdbscan_model = HDBSCAN(min_cluster_size=10, min_samples=2, cluster_selection_method='eom')

# The rest of your BERTopic setup remains the same
# Iterate over each subsample and run BERTopic
bertopic_models = {}
for label, df_subsample in subsamples.items():
    # Ensure the text column exists
    if 'text_clean' not in df_subsample.columns:
        print(f"Column 'text_clean' not found in subsample {label}. Skipping...")
        continue
    
    # Encode documents using Sentence Transformer
    documents = df_subsample['text_clean'].tolist()
    document_vectors = model.encode(documents, show_progress_bar=True)
    
    # Initialize CountVectorizer with custom stopwords
    vectorizer = CountVectorizer(stop_words=stopwords_combined)
    
    # Create and fit BERTopic model
    topic_model = BERTopic(language="multilingual", embedding_model=model, umap_model=umap_model,
                           hdbscan_model=hdbscan_model, vectorizer_model=vectorizer, verbose=True)
    
    # Fit the model with the texts and the corresponding embeddings
    topics, probabilities = topic_model.fit_transform(documents, document_vectors)
    
    # Store the model for later access
    bertopic_models[label] = topic_model
    
    # Visualize the top n topics (optional: save the visualization)
    topic_model.visualize_barchart(top_n_topics=10)
    # topic_model.visualize_barchart(top_n_topics=10).write_html(f"{label}_barchart.html")
    
    # Print topic information
    print(topic_model.get_topic_info().head())

# At this point, bertopic_models contains all your models, accessible by their word count range labels.


[nltk_data] Downloading package stopwords to /home/onyxia/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Batches:   0%|          | 0/63 [00:00<?, ?it/s]

2024-03-20 14:31:28,874 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-03-20 14:31:44,553 - BERTopic - Dimensionality - Completed ✓
2024-03-20 14:31:44,555 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-03-20 14:31:44,652 - BERTopic - Cluster - Completed ✓
2024-03-20 14:31:44,658 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-03-20 14:31:44,838 - BERTopic - Representation - Completed ✓


   Topic  Count                                               Name  \
0     -1    443    -1_channel_german_epochtimesdeutschland_beitrag   
1      0    152                                0_berlin_2022_02_24   
2      1     99            1_unzensiert_unzensiertv2_infoseite_gut   
3      2     95  2_epochtimesdeutschland_beitrag_neuer_deutschland   
4      3     59                   3_tagesschau_trump_biden_politik   

                                      Representation  \
0  [channel, german, epochtimesdeutschland, beitr...   
1  [berlin, 2022, 02, 24, 2021, 01, 10, demo, 03,...   
2  [unzensiert, unzensiertv2, infoseite, gut, net...   
3  [epochtimesdeutschland, beitrag, neuer, deutsc...   
4  [tagesschau, trump, biden, politik, politische...   

                                 Representative_Docs  
0  [our channel in german  bulgarian channel , ou...  
1  [der platz füllt sich!münchen 16.03.2022, demo...  
2  [@unzensiert infoseite @unzensiert / @unzensie...  
3  [warum windräder vi

Batches:   0%|          | 0/63 [00:00<?, ?it/s]

...

2024-03-20 14:36:28,270 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-03-20 14:36:38,019 - BERTopic - Dimensionality - Completed ✓
2024-03-20 14:36:38,021 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-03-20 14:36:38,093 - BERTopic - Cluster - Completed ✓
2024-03-20 14:36:38,099 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-03-20 14:36:39,044 - BERTopic - Representation - Completed ✓


   Topic  Count                                Name  \
0     -1    520        -1_mehr_wurde_menschen_immer   
1      0    129             0_covid_corona_19_virus   
2      1     84     1_russland_tonnen_ukraine_putin   
3      2     77          2_video_videos_film_google   
4      3     57  3_channel_russian_german_ukrainian   

                                      Representation  \
0  [mehr, wurde, menschen, immer, ukraine, schon,...   
1  [covid, corona, 19, virus, impfung, dr, corona...   
2  [russland, tonnen, ukraine, putin, russischen,...   
3  [video, videos, film, google, telegram, youtub...   
4  [channel, russian, german, ukrainian, forces, ...   

                                 Representative_Docs  
0  [es war mal die kleine güzey,  die lange zeit ...  
1  [geheime cdc-berichte bestätigen, dass 6 milli...  
2  [  rise of russia : american thinker nannte di...  
3  [  bundesregierung muss stellungnahme an un zu...  
4  [     the highlights of the night:  the europe...  


Batches:   0%|          | 0/63 [00:00<?, ?it/s]

2024-03-20 14:36:46,165 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-03-20 14:36:54,951 - BERTopic - Dimensionality - Completed ✓
2024-03-20 14:36:54,953 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-03-20 14:36:55,021 - BERTopic - Cluster - Completed ✓
2024-03-20 14:36:55,026 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-03-20 14:36:56,553 - BERTopic - Representation - Completed ✓


   Topic  Count                                             Name  \
0     -1    669                       -1_menschen_uhr_wurde_mehr   
1      0     85                      0_menschen_mehr_immer_leben   
2      1     54        1_virus_covid_coronavirus_schutzmaßnahmen   
3      2     53  2_streitkräfte_richtung_russischen_ukrainischen   
4      3     47                  3_video_youtube_videos_pankalla   

                                      Representation  \
0  [menschen, uhr, wurde, mehr, immer, deutschlan...   
1  [menschen, mehr, immer, leben, viele, welt, tu...   
2  [virus, covid, coronavirus, schutzmaßnahmen, s...   
3  [streitkräfte, richtung, russischen, ukrainisc...   
4  [video, youtube, videos, pankalla, film, demo,...   

                                 Representative_Docs  
0  [ montagstermine für den 14.03.2022 in thüring...  
1  [facebookfund     das hab ich gerade von meine...  
2  [jetzt wird es hart.  die fraktionen der cdu/c...  
3  [     sonderchronik der spezial

### step 3: find similar topics across models

In [19]:
def find_similar_topics(word, topic_model):
    similar_topics, similarity = topic_model.find_topics(word, top_n=5)
    topic_info_df = topic_model.get_topic_info()

    print(f"The top 5 topics relating to '{word}' are: ")
    print("")

    for topic, similarity_score in zip(similar_topics, similarity):
        if topic == -1:
            print("Topic number: -1 (Outliers/Noise)")
            print("Similarity score:", similarity_score)
        else:
            name = topic_info_df[topic_info_df.Topic == topic]['Name'].values[0]
            representation = topic_info_df[topic_info_df.Topic == topic]['Representation'].values[0]
            representative_docs = topic_info_df[topic_info_df.Topic == topic]['Representative_Docs'].values[0]
            print(f"Topic number: {topic}")
            print(f"Name of the topic: {name}")
            print(f"Representative words: {representation}")
            print(f"Representative messages: {representative_docs}")
            print(f"Similarity score: {similarity_score}")
        print("----------------------")

In [20]:
keywords = ["wahl", "politik", "elite", "betrug", "volk", "leute", "unterdrückung", "staat", 
            "gewalt", "machtbegrenzung", "schwarmintelligenz", "freiheit", "basis", "Partei", 
            "system", "plandemie", "basisdemokratie", "Demokratie"]

for word in keywords:
    print(f"\nFinding topics similar to '{word}' across all models:")
    for label, topic_model in bertopic_models.items():
        print(f"\nWord Count Range: {label}")
        find_similar_topics(word, topic_model)
    print("\n" + "="*80)



Finding topics similar to 'wahl' across all models:

Word Count Range: 5-10
The top 5 topics relating to 'wahl' are: 

Topic number: 61
Name of the topic: 61_zeitung_fake_news_verbreitet
Representative words: ['zeitung', 'fake', 'news', 'verbreitet', 'kanzler', 'weitergeben', 'ard20', '2024güzey', 'abgeführt', 'abgesagt']
Representative messages: ['schweizer bauer, eine zeitung welche unabhängig recherchiert!', 'leserbrief, kleine zeitung kärnten, 4. 7. 2021', 'bauern-demo eskaliert: auftritt von özdemir abgesagt   berliner zeitung']
Similarity score: 0.2034912258386612
----------------------
Topic number: 53
Name of the topic: 53_claudio_siber_david_reitschuster
Representative words: ['claudio', 'siber', 'david', 'reitschuster', 'online', 'onlinekanal', 'newskanal', 'faz', 'timeskanal', 'oilprice']
Representative messages: ['   faz onlinekanal david claudio siber', '   reitschuster onlinekanal david claudio siber', 'gefunden bei:reitschuster online   kanal david claudio siber']
Simil